# ApLatamNet Webinar #3 - Post-procesamiento

Ahora que ya hemos realizado una predicción sobre imágenes con nuestro modelo pre-entrenado, podemos trabajar sobre los resultados para llegar a datos más reutilizables.

El objetivo es obtener un archivo vectorial (Shapefile, GeoJSON, etc.) de polígonos o multipolígonos, de las áreas detectadas como asentamientos informales. Para esto realizaremos los siguientes pasos:

1. Filtro por umbral
2. Poligonización
3. Filtro de área mínima

Utilizaremos Satproc nuevamente para post procesar los resultados. También instalamos Geopandas.

In [ ]:
!pip install pysatproc geopandas

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
    Preparing wheel metadata ... done
     |████████████████████████████████| 19.3 MB 1.1 MB/s 
     |████████████████████████████████| 6.3 MB 37.4 MB/s 
     |████████████████████████████████| 1.0 MB 36.4 MB/s 
     |████████████████████████████████| 16.7 MB 38.3 MB/s 
  Created wheel for pysatproc: filename=pysatproc-0.1.9-py2.py3-none-any.whl size=35759 sha256=404f76b0401089b4f4e8dfd11a067ca1b73024d22ad91a4517589fa9773e2202
  Stored in directory: /root/.cache/pip/wheels/cb/fd/5e/3353869723db14b8496985de8066a5977b8b5b5317f7079495
Successfully built pysatproc


## Preparación de datos

A efectos de este webinar, nos descargamos primero los resultados de la predicción de la sesión anterior:

In [ ]:
results_dir = "data/results"

In [ ]:
!wget https://storage.googleapis.com/dym-workshops-public/aplatam-net/session3/honduras_predict_results.zip -O results.zip
!mkdir -p $results_dir
!unzip -o -d $results_dir results.zip

--2022-07-20 19:24:36--  https://storage.googleapis.com/dym-workshops-public/aplatam-net/session3/honduras_predict_results.zip
Resolving storage.googleapis.com (storage.googleapis.com)... 74.125.134.128, 74.125.141.128, 173.194.210.128, ...
Connecting to storage.googleapis.com (storage.googleapis.com)|74.125.134.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1096065 (1.0M) [application/zip]
Saving to: ‘results.zip’

results.zip         100%[===================>]   1.04M  --.-KB/s    in 0.009s  

2022-07-20 19:24:36 (122 MB/s) - ‘results.zip’ saved [1096065/1096065]

Archive:  results.zip
  inflating: data/results/honduras_0000000000-0000000000_0_22.tif  
  inflating: data/results/honduras_0000000000-0000000000_0_23.tif  
  inflating: data/results/honduras_0000000000-0000000000_0_24.tif  
  inflating: data/results/honduras_0000000000-0000000000_10_20.tif  
  inflating: data/results/honduras_0000000000-0000000000_10_21.tif  
  inflating: data/results/hondur

## Filtro por umbral

En este paso se filtran las imágenes aplicando un umbral sobre los valores de los píxeles de cada ráster, que en este caso representan la probabilidad (valores entre 0 y 1), quedándonos así con las de mayor precisión.

*Nota*: En realidad `unetseg` al predecir genera rásteres con valores entre 0 y 255, porque utiliza el tipo de datos Byte, que es de 8 bits. Para convertir estos valores entre 0 y 255 a 0.0 y 1.0, simplemente se divide el numero por 255. La razón de esta optimización es porque almacenar números de punto flotante es más costoso que almacenar en bytes (al menos 4 u 8 veces más costoso en espacio).

In [ ]:
from satproc.filter import filter_by_max_prob

In [ ]:
filtered_results_dir = "data/filtered"
threshold = 0.5

In [ ]:
!rm -rf $filtered_results_dir

In [ ]:
filter_by_max_prob(input_dir=results_dir,
                   output_dir=filtered_results_dir,
                   threshold=threshold)

100%|##########| 457/457 [00:01<00:00, 364.70it/s]


## Poligonizado

La siguiente función aplica una rutina de poligonización sobre los resultados de la predicción del modelo y genera un archivo vectorial en formato GeoPackage (GPKG). La rutina utiliza `gdal_polygonize.py` sobre cada chip resultado generando un GPKG para cada chip, y luego une todos estos archivos en uno solo y disuelve las geometrías, de manera eficiente.

Antes de unirlos también aplica un umbral sobre los valores de los rásteres, que en este caso representan la probabilidad (valores entre 0 y 1). Utilizaremos el mismo umbral que usamos en el paso anterior de filtrado.

In [ ]:
from satproc.postprocess.polygonize import polygonize

In [ ]:
polygonized_results_path = "data/polygonized.gpkg"

In [ ]:
polygonize(threshold=threshold,
           input_dir=filtered_results_dir,
           output=polygonized_results_path)

Dissolve: 100%|##########| 5/5 [00:02<00:00,  2.32it/s]


In [ ]:
import folium
import geopandas as gpd

In [ ]:
geojson_path = "data/polygonized.geojson"

gpd.read_file(polygonized_results_path).to_file(geojson_path, driver="GeoJSON")

In [ ]:
m = folium.Map(location=[14.073297, -87.202824], zoom_start=12)
folium.GeoJson(geojson_path, name="geojson").add_to(m)
m

Se puede observar que hay pequeños polígonos causados por falsos positivos que podrían ser eliminados.

## Filtrar por área mínima

Para resolver este problema, como último paso, filtramos aquellos polígonos de area inferior a 3000 m². Para esto utilizamos GeoPandas para reproyectar a un CRS proyectado con unidad en metros (esto es necesario porque que las imágenes tenían el geográfico WGS84, EPSG:4326) y luego filtrar el dataframe para quedarnos con los polígonos con area mayor al umbral.

In [ ]:
utm_polygonized_path = "data/polygonized_utm.gpkg"

# Reproyectamos a EPSG:32616, que corresponde a la zona UTM de Tegucigalpa.
gdf = gpd.read_file(polygonized_results_path).to_crs("epsg:32616")
gdf

DN                                           geometry
0     255  POLYGON ((466043.546 1556002.066, 466053.244 1...
1     255  POLYGON ((465820.493 1556002.364, 465820.480 1...
2     255  POLYGON ((465723.513 1556002.495, 465733.211 1...
3     255  POLYGON ((465752.741 1556101.807, 465762.439 1...
4     255  POLYGON ((465694.486 1556052.210, 465704.184 1...
...   ...                                                ...
2139  255  POLYGON ((484704.364 1559371.842, 484694.668 1...
2140  255  POLYGON ((484694.674 1559381.783, 484684.977 1...
2141  255  POLYGON ((484762.550 1559381.742, 484762.544 1...
2142  255  POLYGON ((484714.067 1559381.771, 484714.073 1...
2143  255  POLYGON ((484704.400 1559431.452, 484714.097 1...

[2144 rows x 2 columns]

In [ ]:
output_path = "data/output.gpkg"
min_area = 3000

gdf = gdf[gdf.geometry.area >= min_area]
gdf

DN                                           geometry
3     255  POLYGON ((465752.741 1556101.807, 465762.439 1...
13    255  POLYGON ((466053.417 1556131.209, 466053.430 1...
52    255  POLYGON ((466103.032 1556975.630, 466103.045 1...
77    255  POLYGON ((394793.728 1702101.870, 394793.773 1...
157   255  POLYGON ((468873.649 1554607.530, 468863.950 1...
...   ...                                                ...
1966  255  POLYGON ((484024.360 1557395.189, 484024.367 1...
2020  255  POLYGON ((484673.045 1555676.032, 484673.051 1...
2028  255  POLYGON ((484634.415 1555944.300, 484624.717 1...
2045  255  POLYGON ((484674.141 1557494.139, 484674.147 1...
2077  255  POLYGON ((484966.019 1559113.375, 484966.024 1...

[79 rows x 2 columns]

In [ ]:
gdf.to_crs("epsg:4326").to_file(output_path, driver="GPKG")

Resultado final:

In [ ]:
filt_geojson_path = "data/output.geojson"
gpd.read_file(output_path).to_file(filt_geojson_path, driver="GeoJSON")

In [ ]:
m = folium.Map(location=[14.073297, -87.202824], zoom_start=12)
folium.GeoJson(geojson_path, name="original").add_to(m)
folium.GeoJson(filt_geojson_path, name="filtrado", style_function=lambda x: {'fillColor': '#ff0000', 'color': '#ff0000'}).add_to(m)
folium.LayerControl().add_to(m)
m